In [1]:
import h5py
import scipy.sparse as ss
import os
import sys
import numpy as np
import pandas as pd
import h5py
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
from scipy.sparse import csr_matrix, dia_matrix, triu, tril, coo_matrix
import pyranges as pr
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler


def get_network_type(hfile, network=None):
    if not os.path.exists(hfile):
        raise ValueError('hfile must be a path pointing to a '
                         'readable HDF5 file.')
    with h5py.File(hfile, 'r') as hf:
        if 'aggregates' in hf.keys() and 'networks' in hf.keys():
            raise ValueError(layout_error_msg('contains both "aggregates" '
                                'and "networks" as top level groups.'))
        elif 'aggregates' in hf.keys():
            net_group = 'aggregates'
        elif 'networks' in hf.keys():
            net_group = 'networks'
        else:
            raise ValueError(layout_error_msg('contains both "aggregates" '
                                'and "networks" as top level groups.'))
        if network is not None:
            if (network not in hf[f'/{net_group}'].keys()
                    or type(hf[f'/{net_group}/{network}'])
                    is not h5py._hl.group.Group):
                raise ValueError(layout_error_msg('network must be an HDF5 '
                                    f'Group under \'/{net_group}/\''))
            return net_group, network
        else:
            return net_group



INFO:numexpr.utils:Note: detected 192 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 192 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [26]:
import time
import matplotlib.pyplot as plt
import seaborn as sns


import scanpy as sc
import anndata



import importlib

import pandas as pd
import numpy as np

In [27]:
fn='/grid/gillis/data_norepl/lohia/BICCN_enhancer_challenege/10XMultiome/Mouse/Mouse_atac.h5ad'

In [28]:
adata_orig = sc.read_h5ad(fn)

In [11]:
base_folder='/grid/gillis/data_norepl/'

In [24]:
hfile = f'{base_folder}/lohia/hi_c_data_processing/data_mouse/500kbp_raw/aggregate.hdf5'

In [22]:
chr_list=list(range(1,2))

In [ ]:
${inp_path}/${NETWORK}/aggregate.hdf5

In [ ]:
       python ${software_path}/convert_fox_to_gene_vector.py \
       --base_folder $base_folder \
       --resolution_human_format $resolution_human \
       --resolution_network $NETWORK \
       --SRP $SRP_name \
       --candidate_h5_file aggregate.hdf5 \
       --chr_list ${chrom_list} \
       --chrom_size_folder $CHROMS \
       --input_path ${inp_path}/${NETWORK}/aggregate.hdf5 \
       --contacts_type ${ice_type} \
       --outfile_path_net ${c_path}/${NETWORK}/max/ \
       --matrix_dtype ${dtype} \
       --species ${species} \
       --genome_info_file ${base_folder}/lohia/hi_c_data_processing/genomes_jlee/${GENOME} \
       --exp_file_path ${base_folder}/lohia/hi_c_data_processing/software/CoCoCoNet/networks/${species}_prioAggNet.h5

In [25]:
    
    with h5py.File(hfile, 'r') as hfile:
        print ('l')
        chrom_l = []
        bin_id_abs=[]
        bin_id_end=[]
        gene_id=[]
        chrom_gene_id_dict = {}

        
        chrom_sizes_from_matrix = []
        for chrom_i in chr_list:
            counter = 0
            #gene_chrom = gene_data_grouped_chromosome.get_group(chrom_i)
            #matrix_per_chrom_gene_by_bin = []
            #matrix_per_chrom_gene_by_gene = []
            
            
            
            #matrix_cols = []
            #for chrom_j in chr_list[counter::]:
            for chrom_j in chr_list:
                counter = counter + 1


                #sparse.coo_matrix((3, 4))
                chrom = 'chr1' + '_vs_' + 'chr2'
                if not chrom.startswith('chr'):
                    continue
                chrom_path = f'/{net_group}/{network}/{chrom}'
                #print (hfile[f'{chrom_path}/shape'][:])
                try:
                    matrix = ss.coo_matrix((hfile[f'{chrom_path}/data'][:],
                                            (hfile[f'{chrom_path}/row'][:],
                                            hfile[f'{chrom_path}/col'][:])),
                                        hfile[f'{chrom_path}/shape'][:])
                    matrix = matrix.astype('uint32')

                except Exception as e:
                    chrom = chrom_j + '_vs_' + chrom_i
                    chrom_path = f'/{net_group}/{network}/{chrom}'
                    #print ("here")
                    matrix = ss.coo_matrix((hfile[f'{chrom_path}/data'][:],
                                            (hfile[f'{chrom_path}/row'][:],
                                            hfile[f'{chrom_path}/col'][:])),
                                        hfile[f'{chrom_path}/shape'][:])

l


NameError: name 'net_group' is not defined

In [ ]:
def get_all_chrom_contacts(exp_file_path, outfile, species, resolution_human_format, genome_info_file, hfile, network, chr_list, contacts_type, matrix_dtype, fmt='coo'):
    
    
    gr = pr.read_gtf(genome_info_file)
    df = gr.df
    gene_data = df[df['Feature'] == 'gene']
    gene_data['gene_id'] = [x.split('.')[0] for x in gene_data['gene_id']]
    gene_data['gene_id'].drop_duplicates(inplace=True)
    

    
    if species != 'human':
        gene_data['Chromosome'] = ['chr'+x for x in gene_data['Chromosome']]
        
    new = gene_data["Chromosome"].isin(chr_list)
  

    gene_data = gene_data[new]
    gene_data.sort_values(by=['Chromosome', 'Start'], inplace=True)
            
    gene_data = gene_data[gene_data['Chromosome'].isin(chr_list)] 
    
    exp_file = hm.hiCMatrix(exp_file_path)
    exp_genes_all = [x[3].decode() for x in exp_file.cut_intervals]

    gene_data = gene_data[gene_data['gene_id'].isin(exp_genes_all)]

    gene_data_grouped_chromosome = gene_data.groupby('Chromosome')
    
    
    valid_fmts = {'bsr', 'coo', 'csc', 'csr', 'dia', 'dok', 'lil'}
    if fmt not in valid_fmts:
        raise ValueError(f'{fmt} is not a valid format.')
    net_group, network = get_network_type(hfile, network)
    
    print (hfile)
    
    outfile_name = f'{outfile}hic_gene_gw_none_by_allbins_none.h5'
    
    if os.path.isfile(outfile_name):
        os.remove(outfile_name)
        

    
    with h5py.File(hfile, 'r') as hfile:
        chrom_l = []
        bin_id_abs=[]
        bin_id_end=[]
        gene_id=[]
        chrom_gene_id_dict = {}

        
        chrom_sizes_from_matrix = []
        for chrom_i in chr_list:
            counter = 0
            gene_chrom = gene_data_grouped_chromosome.get_group(chrom_i)
            matrix_per_chrom_gene_by_bin = []
            matrix_per_chrom_gene_by_gene = []
            
            
            
            #matrix_cols = []
            #for chrom_j in chr_list[counter::]:
            for chrom_j in chr_list:
                counter = counter + 1


                #sparse.coo_matrix((3, 4))
                chrom = chrom_i + '_vs_' + chrom_j
                if not chrom.startswith('chr'):
                    continue
                chrom_path = f'/{net_group}/{network}/{chrom}'
                #print (hfile[f'{chrom_path}/shape'][:])
                try:
                    matrix = ss.coo_matrix((hfile[f'{chrom_path}/data'][:],
                                            (hfile[f'{chrom_path}/row'][:],
                                            hfile[f'{chrom_path}/col'][:])),
                                        hfile[f'{chrom_path}/shape'][:])
                    matrix = matrix.astype('uint32')

                except Exception as e:
                    chrom = chrom_j + '_vs_' + chrom_i
                    chrom_path = f'/{net_group}/{network}/{chrom}'
                    #print ("here")
                    matrix = ss.coo_matrix((hfile[f'{chrom_path}/data'][:],
                                            (hfile[f'{chrom_path}/row'][:],
                                            hfile[f'{chrom_path}/col'][:])),
                                        hfile[f'{chrom_path}/shape'][:])
                    
                    matrix = matrix.T
                    matrix = matrix.astype('uint32')

                if contacts_type == 'gw':
                        
                        if chrom_i == chrom_j:
                            if ss.tril(matrix, k=-1).sum() == 0:
                                matrix = matrix + ss.triu(matrix, 1).T
                            else:
                                pass
                            
                        else:
                            pass
                elif contacts_type == 'intra':
                        
                        if chrom_i != chrom_j:
                            matrix = matrix * 0
                        else:
                            pass
                        
                elif contacts_type == 'inter':
                        
                        if chrom_i == chrom_j:
                            matrix = matrix * 0
                        else:
                            pass
                
                else:
                        pass

                matrix_per_chrom_pair = ss.csr_matrix(matrix, dtype=np.uint32)